In [ ]:
import pandas as pd
import numpy as np

pd.set_option('display.max_columns', 500)

#train
df = pd.read_csv("./input/train.csv")
df.drop(['start_square', 'plan_s', 'plan_m', 'plan_l', 'vid_0', 'vid_1', 'vid_2'], axis=1, inplace=True)
df.to_csv("./input/train_full.csv", index=False)

#test
dt = pd.read_csv("./input/test.csv")
dt['value'] = 0
dt.to_csv("./input/test_.csv", index=False, columns = df.columns)

In [1]:
#valid
from sklearn.model_selection import KFold
import pandas as pd
df = pd.read_csv("./input/train_full.csv")

kf = KFold(n_splits=10, random_state=42, shuffle=True)
kf.get_n_splits(range(len(df)))

print(kf)  

for i, (train_index, valid_index) in enumerate(kf.split(range(len(df)))):
    train = df.loc[train_index]
    valid = df.loc[valid_index]

    train.to_csv(f"./input/train_{i}.csv",index=False)
    valid.to_csv(f"./input/valid_{i}.csv",index=False)

KFold(n_splits=10, random_state=42, shuffle=True)


In [2]:
K = 10

from catboost import CatBoostRegressor, Pool
import pandas as pd
import numpy as np

path = './input/'

TEST_FILE = path + 'test_.csv' #add
CD_FILE = path + 'train.cd'

test_pool = Pool(TEST_FILE, column_description=CD_FILE, has_header=True, delimiter=",")

df = pd.read_csv('./input/train_full.csv')
oof = np.zeros((len(df), 1))

dt = pd.read_csv(TEST_FILE)
test = np.zeros((len(dt), 1))

for i in range(K):

    TRAIN_FILE = path+f'train_{i}.csv'
    VAL_FILE = path+f'valid_{i}.csv'

    train_pool = Pool(TRAIN_FILE, column_description=CD_FILE, has_header=True, delimiter=",")
    val_pool = Pool(VAL_FILE, column_description=CD_FILE, has_header=True, delimiter=",")

    model = CatBoostRegressor(iterations=5000, 
                              learning_rate=0.05, 
                              depth=10, 
                              random_seed = 42)
    
    model.fit(train_pool, eval_set = val_pool)
    
    pred = model.predict(test_pool)
    test += pred.reshape((len(dt),1))
    dt['value'] = pred
    dt.to_csv(f"./output/test_{i}.csv", index=False, columns=['id','value'])
    
    pred = model.predict(val_pool)
    df = pd.read_csv(VAL_FILE)
    oof[df.id] = pred.reshape((len(df),1))
    df['value'] = pred
    df.to_csv(f"./output/oof_{i}.csv", index=False, columns=['id','value'])
    
df = pd.read_csv(path+"sample submission.csv")
df['value'] = (test/K).clip(0, 5000)
df.to_csv("./output/sub.csv", index=False)

df = pd.read_csv(path+"train_full.csv")
df['value_pred'] = oof
df.to_csv("./output/oof.csv", index=False)

0:	learn: 453.0494799	test: 444.4819109	best: 444.4819109 (0)	total: 56ms	remaining: 4m 39s
1:	learn: 444.1769824	test: 435.4429211	best: 435.4429211 (1)	total: 62.8ms	remaining: 2m 36s
2:	learn: 434.7659387	test: 425.7938955	best: 425.7938955 (2)	total: 96.5ms	remaining: 2m 40s
3:	learn: 425.6154983	test: 417.0699106	best: 417.0699106 (3)	total: 133ms	remaining: 2m 46s
4:	learn: 416.7858117	test: 408.4843643	best: 408.4843643 (4)	total: 173ms	remaining: 2m 53s
5:	learn: 408.7718990	test: 400.4890415	best: 400.4890415 (5)	total: 209ms	remaining: 2m 54s
6:	learn: 401.0619935	test: 393.1011432	best: 393.1011432 (6)	total: 234ms	remaining: 2m 46s
7:	learn: 394.4036844	test: 386.2239364	best: 386.2239364 (7)	total: 262ms	remaining: 2m 43s
8:	learn: 388.1115805	test: 379.9646083	best: 379.9646083 (8)	total: 301ms	remaining: 2m 46s
9:	learn: 382.3670473	test: 374.1488542	best: 374.1488542 (9)	total: 312ms	remaining: 2m 35s
10:	learn: 377.7015555	test: 369.5653472	best: 369.5653472 (10)	total

88:	learn: 261.2160663	test: 263.3616646	best: 263.3616646 (88)	total: 2.37s	remaining: 2m 11s
89:	learn: 260.5062712	test: 262.6125008	best: 262.6125008 (89)	total: 2.41s	remaining: 2m 11s
90:	learn: 259.8674953	test: 262.0070381	best: 262.0070381 (90)	total: 2.45s	remaining: 2m 12s
91:	learn: 259.6965356	test: 261.9357116	best: 261.9357116 (91)	total: 2.48s	remaining: 2m 12s
92:	learn: 258.9729935	test: 261.4095604	best: 261.4095604 (92)	total: 2.51s	remaining: 2m 12s
93:	learn: 258.3871023	test: 260.9735910	best: 260.9735910 (93)	total: 2.56s	remaining: 2m 13s
94:	learn: 257.7728646	test: 260.9252436	best: 260.9252436 (94)	total: 2.59s	remaining: 2m 13s
95:	learn: 257.4396885	test: 260.6896176	best: 260.6896176 (95)	total: 2.62s	remaining: 2m 13s
96:	learn: 256.6610178	test: 260.0251769	best: 260.0251769 (96)	total: 2.65s	remaining: 2m 13s
97:	learn: 256.1762697	test: 259.5897699	best: 259.5897699 (97)	total: 2.68s	remaining: 2m 13s
98:	learn: 256.0110204	test: 259.5291226	best: 259

174:	learn: 225.9344117	test: 242.9376717	best: 242.9376717 (174)	total: 4.8s	remaining: 2m 12s
175:	learn: 225.7540859	test: 242.8427563	best: 242.8427563 (175)	total: 4.83s	remaining: 2m 12s
176:	learn: 225.4227457	test: 242.6686502	best: 242.6686502 (176)	total: 4.86s	remaining: 2m 12s
177:	learn: 225.1013365	test: 242.6142857	best: 242.6142857 (177)	total: 4.89s	remaining: 2m 12s
178:	learn: 224.8269951	test: 242.6219668	best: 242.6142857 (177)	total: 4.91s	remaining: 2m 12s
179:	learn: 224.4909581	test: 242.6399791	best: 242.6142857 (177)	total: 4.94s	remaining: 2m 12s
180:	learn: 224.2150538	test: 242.3626800	best: 242.3626800 (180)	total: 4.97s	remaining: 2m 12s
181:	learn: 223.8112084	test: 242.1753230	best: 242.1753230 (181)	total: 4.99s	remaining: 2m 12s
182:	learn: 223.5707710	test: 242.1936430	best: 242.1753230 (181)	total: 5.02s	remaining: 2m 12s
183:	learn: 223.1596142	test: 241.8478880	best: 241.8478880 (183)	total: 5.05s	remaining: 2m 12s
184:	learn: 222.8363875	test: 2

265:	learn: 200.3524125	test: 230.6812662	best: 230.6812662 (265)	total: 7.65s	remaining: 2m 16s
266:	learn: 199.9575566	test: 230.6172691	best: 230.6172691 (266)	total: 7.68s	remaining: 2m 16s
267:	learn: 199.9205537	test: 230.6053596	best: 230.6053596 (267)	total: 7.71s	remaining: 2m 16s
268:	learn: 199.5833213	test: 230.4421708	best: 230.4421708 (268)	total: 7.75s	remaining: 2m 16s
269:	learn: 199.4866485	test: 230.3756183	best: 230.3756183 (269)	total: 7.78s	remaining: 2m 16s
270:	learn: 199.3424557	test: 230.2794813	best: 230.2794813 (270)	total: 7.81s	remaining: 2m 16s
271:	learn: 199.2061537	test: 230.1608700	best: 230.1608700 (271)	total: 7.84s	remaining: 2m 16s
272:	learn: 199.0006240	test: 229.9622456	best: 229.9622456 (272)	total: 7.88s	remaining: 2m 16s
273:	learn: 198.7642971	test: 229.7170106	best: 229.7170106 (273)	total: 7.91s	remaining: 2m 16s
274:	learn: 198.5904761	test: 229.6393101	best: 229.6393101 (274)	total: 7.94s	remaining: 2m 16s
275:	learn: 198.5047849	test: 

354:	learn: 186.0383300	test: 224.3326122	best: 224.3313037 (353)	total: 10.5s	remaining: 2m 17s
355:	learn: 185.9206022	test: 224.0151115	best: 224.0151115 (355)	total: 10.5s	remaining: 2m 17s
356:	learn: 185.8172401	test: 223.9316288	best: 223.9316288 (356)	total: 10.6s	remaining: 2m 17s
357:	learn: 185.7097802	test: 223.9312657	best: 223.9312657 (357)	total: 10.6s	remaining: 2m 17s
358:	learn: 185.3212703	test: 223.4829691	best: 223.4829691 (358)	total: 10.7s	remaining: 2m 17s
359:	learn: 185.2264183	test: 223.4119442	best: 223.4119442 (359)	total: 10.7s	remaining: 2m 17s
360:	learn: 185.0614188	test: 223.2521365	best: 223.2521365 (360)	total: 10.7s	remaining: 2m 17s
361:	learn: 184.8551434	test: 223.2236041	best: 223.2236041 (361)	total: 10.8s	remaining: 2m 17s
362:	learn: 184.7142704	test: 223.1345780	best: 223.1345780 (362)	total: 10.8s	remaining: 2m 17s
363:	learn: 184.6210609	test: 223.0247451	best: 223.0247451 (363)	total: 10.8s	remaining: 2m 17s
364:	learn: 184.6044850	test: 

...

4590:	learn: 57.5791207	test: 243.6329875	best: 243.6079254 (4587)	total: 1m 59s	remaining: 10.7s
4591:	learn: 57.5750527	test: 243.6299019	best: 243.6079254 (4587)	total: 1m 59s	remaining: 10.6s
4592:	learn: 57.5708433	test: 243.6327624	best: 243.6079254 (4587)	total: 1m 59s	remaining: 10.6s
4593:	learn: 57.5614221	test: 243.6299442	best: 243.6079254 (4587)	total: 1m 59s	remaining: 10.6s
4594:	learn: 57.5584649	test: 243.6306539	best: 243.6079254 (4587)	total: 1m 59s	remaining: 10.6s
4595:	learn: 57.5382766	test: 243.6370896	best: 243.6079254 (4587)	total: 1m 59s	remaining: 10.5s
4596:	learn: 57.5376357	test: 243.6355906	best: 243.6079254 (4587)	total: 1m 59s	remaining: 10.5s
4597:	learn: 57.5264185	test: 243.6445407	best: 243.6079254 (4587)	total: 1m 59s	remaining: 10.5s
4598:	learn: 57.5263973	test: 243.6447011	best: 243.6079254 (4587)	total: 1m 59s	remaining: 10.5s
4599:	learn: 57.5242742	test: 243.6459184	best: 243.6079254 (4587)	total: 2m	remaining: 10.4s
4600:	learn: 57.5221268	

4678:	learn: 56.7621384	test: 243.6085268	best: 243.6004816 (4620)	total: 2m 2s	remaining: 8.38s
4679:	learn: 56.7541838	test: 243.6082758	best: 243.6004816 (4620)	total: 2m 2s	remaining: 8.35s
4680:	learn: 56.7529990	test: 243.6081755	best: 243.6004816 (4620)	total: 2m 2s	remaining: 8.32s
4681:	learn: 56.7401901	test: 243.6125712	best: 243.6004816 (4620)	total: 2m 2s	remaining: 8.3s
4682:	learn: 56.7324178	test: 243.6075064	best: 243.6004816 (4620)	total: 2m 2s	remaining: 8.27s
4683:	learn: 56.7205345	test: 243.6074450	best: 243.6004816 (4620)	total: 2m 2s	remaining: 8.24s
4684:	learn: 56.7182088	test: 243.6099475	best: 243.6004816 (4620)	total: 2m 2s	remaining: 8.22s
4685:	learn: 56.7016999	test: 243.6015877	best: 243.6004816 (4620)	total: 2m 2s	remaining: 8.19s
4686:	learn: 56.6931284	test: 243.5990789	best: 243.5990789 (4686)	total: 2m 2s	remaining: 8.16s
4687:	learn: 56.6770903	test: 243.6022923	best: 243.5990789 (4686)	total: 2m 2s	remaining: 8.14s
4688:	learn: 56.6701150	test: 2

4771:	learn: 55.8091546	test: 243.5290418	best: 243.5262750 (4766)	total: 2m 4s	remaining: 5.95s
4772:	learn: 55.8067782	test: 243.5305331	best: 243.5262750 (4766)	total: 2m 4s	remaining: 5.92s
4773:	learn: 55.8014326	test: 243.5345926	best: 243.5262750 (4766)	total: 2m 4s	remaining: 5.89s
4774:	learn: 55.7759738	test: 243.5201187	best: 243.5201187 (4774)	total: 2m 4s	remaining: 5.87s
4775:	learn: 55.7756332	test: 243.5203766	best: 243.5201187 (4774)	total: 2m 4s	remaining: 5.84s
4776:	learn: 55.7744145	test: 243.5207225	best: 243.5201187 (4774)	total: 2m 4s	remaining: 5.81s
4777:	learn: 55.7667277	test: 243.5191831	best: 243.5191831 (4777)	total: 2m 4s	remaining: 5.79s
4778:	learn: 55.7608229	test: 243.5221662	best: 243.5191831 (4777)	total: 2m 4s	remaining: 5.76s
4779:	learn: 55.7381155	test: 243.5312955	best: 243.5191831 (4777)	total: 2m 4s	remaining: 5.74s
4780:	learn: 55.7267706	test: 243.5438072	best: 243.5191831 (4777)	total: 2m 4s	remaining: 5.71s
4781:	learn: 55.7173535	test: 

4862:	learn: 55.0593832	test: 243.5036124	best: 243.4916399 (4814)	total: 2m 6s	remaining: 3.57s
4863:	learn: 55.0394196	test: 243.5001113	best: 243.4916399 (4814)	total: 2m 6s	remaining: 3.54s
4864:	learn: 55.0362500	test: 243.4922337	best: 243.4916399 (4814)	total: 2m 6s	remaining: 3.52s
4865:	learn: 55.0153863	test: 243.4975115	best: 243.4916399 (4814)	total: 2m 6s	remaining: 3.49s
4866:	learn: 55.0141761	test: 243.4972553	best: 243.4916399 (4814)	total: 2m 6s	remaining: 3.47s
4867:	learn: 55.0109953	test: 243.4973895	best: 243.4916399 (4814)	total: 2m 6s	remaining: 3.44s
4868:	learn: 55.0050002	test: 243.4985042	best: 243.4916399 (4814)	total: 2m 6s	remaining: 3.42s
4869:	learn: 54.9975280	test: 243.4974180	best: 243.4916399 (4814)	total: 2m 6s	remaining: 3.39s
4870:	learn: 54.9962997	test: 243.4976439	best: 243.4916399 (4814)	total: 2m 7s	remaining: 3.36s
4871:	learn: 54.9961530	test: 243.4977352	best: 243.4916399 (4814)	total: 2m 7s	remaining: 3.34s
4872:	learn: 54.9875977	test: 

4952:	learn: 54.3902692	test: 243.4409411	best: 243.4405711 (4951)	total: 2m 9s	remaining: 1.23s
4953:	learn: 54.3862637	test: 243.4403830	best: 243.4403830 (4953)	total: 2m 9s	remaining: 1.2s
4954:	learn: 54.3752843	test: 243.4519707	best: 243.4403830 (4953)	total: 2m 9s	remaining: 1.17s
4955:	learn: 54.3737910	test: 243.4539411	best: 243.4403830 (4953)	total: 2m 9s	remaining: 1.15s
4956:	learn: 54.3661464	test: 243.4501283	best: 243.4403830 (4953)	total: 2m 9s	remaining: 1.12s
4957:	learn: 54.3644855	test: 243.4489412	best: 243.4403830 (4953)	total: 2m 9s	remaining: 1.09s
4958:	learn: 54.3558548	test: 243.4395222	best: 243.4395222 (4958)	total: 2m 9s	remaining: 1.07s
4959:	learn: 54.3557493	test: 243.4394826	best: 243.4394826 (4959)	total: 2m 9s	remaining: 1.04s
4960:	learn: 54.3545860	test: 243.4394715	best: 243.4394715 (4960)	total: 2m 9s	remaining: 1.02s
4961:	learn: 54.3527408	test: 243.4424770	best: 243.4394715 (4960)	total: 2m 9s	remaining: 991ms
4962:	learn: 54.3380448	test: 2